In [4]:
import pandas as pd
import numpy as np
import geopandas as gpd
from keplergl import KeplerGl
import json
import sys
print(sys.executable)

with open('../config/kepler_config.json', 'r') as f:
    config = json.load(f)

data_path = '../data/311/2023.csv'
df = pd.read_csv(data_path, parse_dates=['open_dt', 'closed_dt'], low_memory=False)
df = df.dropna(subset=['closed_dt', 'open_dt', 'neighborhood', 'precinct', 'city_council_district', 'location_zipcode'])

neighborhood_gj_path = '../data/geojson/Boston_Neighborhood_Boundaries_Approximated_by_2020_Census_Tracts.geojson'
neighborhood_geo_data = gpd.read_file(neighborhood_gj_path)

precinct_gj_path = '../data/geojson/Boston_Precinct_Boundaries.geojson'
precinct_geo_data = gpd.read_file(precinct_gj_path)

city_council_gj_path = '../data/geojson/City_Council_Districts_-_Current.geojson'
city_council_geo_data = gpd.read_file(city_council_gj_path)

zip_code_gj_path = '../data/geojson/ZIP_Codes.geojson'
zip_code_geo_data = gpd.read_file(zip_code_gj_path)

reasons = df['reason'].value_counts().head(5).index.tolist()
print(reasons)


print(neighborhood_geo_data['neighborhood'].head().tolist())
print(precinct_geo_data['DISTRICT'].head().tolist())
print(city_council_geo_data['Councillor'].head().tolist())
print(zip_code_geo_data['ZIP5'].head().tolist())


['Sanitation', 'Enforcement & Abandoned Vehicles', 'Street Cleaning', 'Code Enforcement', 'Highway Maintenance']
['Allston', 'Back Bay', 'Beacon Hill', 'Brighton', 'Charlestown']
['01-01', '01-02', '01-03', '01-04', '01-05']
['Councillor LaMattina', 'Councillor Linehan', 'Councillor Baker', 'Councillor Campbell', 'Councillor McCarthy']
['02134', '02125', '02110', '02118', '02126']


In [5]:
with open('../config/neighborhood_config.json', 'r') as f:
    config = json.load(f)
neighborhood_map = KeplerGl(height=600, show_docs=False)

for reason in reasons:
    reason_df = df[df['reason'] == reason].copy()
    reason_df['closure_time'] = (reason_df['closed_dt'] - reason_df['open_dt']).dt.days
    
    grouped_data = reason_df.groupby('neighborhood')['closure_time'].mean().reset_index()
    
    merged_data = neighborhood_geo_data.merge(grouped_data, left_on='neighborhood', right_on='neighborhood')
    
    neighborhood_map.add_data(data=merged_data, name=f"{reason} by Neighborhood")

neighborhood_map


KeplerGl(data={'Sanitation by Neighborhood': {'index': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15],…

In [3]:
with open('../config/zipcode_config.json', 'r') as f:
    config = json.load(f)

geo_zip_codes = set(zip_code_geo_data['ZIP5'].unique())

zip_code_map = KeplerGl(height=600, config=config, show_docs=False)

for reason in reasons:
    reason_df = df[df['reason'] == reason].copy()
    reason_df['closure_time'] = (reason_df['closed_dt'] - reason_df['open_dt']).dt.days

    reason_df['location_zipcode'] = reason_df['location_zipcode'].astype(float).astype(int).astype(str).str.zfill(5)
    
    print(reason_df['location_zipcode'].head().tolist())
    
    reason_df = reason_df[reason_df['location_zipcode'].isin(geo_zip_codes)]
    
    grouped_data = reason_df.groupby('location_zipcode')['closure_time'].mean().reset_index()
    
    merged_data = zip_code_geo_data.merge(grouped_data, left_on='ZIP5', right_on='location_zipcode')
    
    zip_code_map.add_data(data=merged_data, name=f"{reason} by Zip Code")

zip_code_map


['02132', '02108', '02127', '02130', '02116']
['02127', '02135', '02127', '02135', '02127']
['02114', '02135', '02118', '02124', '02114']
['02136', '02116', '02111', '02125', '02114']
['02124', '02124', '02127', '02114', '02127']


KeplerGl(config={'version': 'v1', 'config': {'visState': {'layers': [{'type': 'geojson', 'config': {'dataId': …

In [8]:
precinct_map = KeplerGl(height=600, config=config, show_docs=False)

for reason in reasons:
    reason_df = df[df['reason'] == reason].copy()
    reason_df['closure_time'] = (reason_df['closed_dt'] - reason_df['open_dt']).dt.days
    
    grouped_data = reason_df.groupby('precinct')['closure_time'].mean().reset_index()
    
    merged_data = precinct_geo_data.merge(grouped_data, left_on='WDPCT', right_on='precinct')
    
    precinct_map.add_data(data=merged_data, name=f"{reason} by precinct")

precinct_map


/Users/markmaci/miniconda3/lib/python3.11/site-packages/IPython/core/formatters.py:367: FormatterWarning: text/html formatter returned invalid type <class 'bytes'> (expected <class 'str'>) for object: KeplerGl(config={'version': 'v1', 'config': {'visState': {'layers': [{'type': 'geojson', 'config': {'dataId': 'choropleth_layer', 'label': 'Closure Rate by ZIP Code', 'color': [255, 0, 0], 'columns': {'geojson': 'geometry'}, 'isVisible': True, 'visConfig': {'opacity': 0.8, 'strokeOpacity': 0.8, 'thickness': 0.5, 'strokeColor': [255, 255, 255], 'colorRange': {'name': 'Uber Viz Diverging 3.5', 'type': 'diverging', 'category': 'Uber', 'colors': ['#1A3177', '#525AA6', '#9FA7C3', '#D3D1D0', '#E19C5B', '#B75511', '#7C2400'], 'reversed': True}, 'strokeColorRange': {'name': 'Global Warming', 'type': 'sequential', 'category': 'Uber', 'colors': []}, 'radius': 10, 'sizeRange': [0, 10], 'radiusRange': [0, 50], 'heightRange': [0, 500], 'elevationScale': 5, 'stroked': True, 'filled': True, 'enable3d': 

KeplerGl(config={'version': 'v1', 'config': {'visState': {'layers': [{'type': 'geojson', 'config': {'dataId': …